In [24]:
#Data Exercise 1, part A- List of male patients

import sqlite3
import numpy as np

conn = None
cursor = None

try:
    conn = sqlite3.connect('openmrs.db')
    cursor = conn.cursor()
    cursor.execute(''' 
        SELECT *
        FROM patient
        WHERE gender = 'M'
    ''')
    data = np.array(cursor.fetchall()) 
   
    print(' '.join(['gender', 'mrm', 'id', 'birthdate', 'birthdate_estimate']))
    print_friendly_data = "\n".join([", ".join(row) for row in data])
    print (print_friendly_data)
    
except Error:
    print(f'Error occurred reading openmrs data {Error}')

finally:
    cursor.close()
    conn.close()


gender mrm id birthdate birthdate_estimate
M, MRN000002, 2, 1941-05-01, 0
M, MRN000006, 6, 1962-04-21, 0
M, MRN000013, 13, 1974-11-02, 1
M, MRN000016, 16, 1971-06-27, 0
M, MRN000017, 17, 1995-10-24, 0
M, MRN000018, 18, 2003-10-11, 0
M, MRN000020, 20, 2003-06-21, 1
M, MRN000036, 36, 1976-09-16, 1
M, MRN000039, 39, 1964-08-18, 0
M, MRN000044, 44, 1966-01-02, 1
M, MRN000048, 48, 1975-02-14, 1
M, MRN000053, 53, 1966-12-02, 0
M, MRN000065, 65, 1978-07-08, 0
M, MRN000075, 75, 1956-07-11, 1
M, MRN000077, 77, 1979-10-20, 1
M, MRN000092, 92, 1984-03-25, 0
M, MRN000095, 95, 2003-05-06, 1
M, MRN000098, 98, 1960-06-13, 1
M, MRN000109, 109, 1966-01-17, 1
M, MRN000118, 118, 1997-09-19, 1
M, MRN000122, 122, 1957-04-17, 0
M, MRN000127, 127, 1970-06-21, 1
M, MRN000131, 131, 1963-05-27, 0
M, MRN000133, 133, 1980-03-13, 1
M, MRN000139, 139, 1987-01-15, 0
M, MRN000141, 141, 1960-03-10, 0
M, MRN000148, 148, 1962-12-17, 0
M, MRN000164, 164, 1960-04-18, 0
M, MRN000174, 174, 1964-03-15, 1
M, MRN000188, 188, 2

In [9]:
#Data Exercise 1, part  B- List Count of patients by gender

import sqlite3
import numpy as np

conn = None
cursor = None

try:
    conn = sqlite3.connect('openmrs.db')
    cursor = conn.cursor()
    cursor.execute(''' 
        SELECT gender, count(gender)
        FROM patient
        GROUP BY gender
    ''')
    data = (cursor.fetchall())
   
    for datum in data:
        gender = ''
        
        if datum[0].strip().lower() == 'm':
            gender = 'Male'
        elif datum[0].strip().lower() == 'f':
            gender = 'Female'
        else:
            gender = 'Unspecified'
            
            
        print(f'{gender}: {datum[1]}')
    
except Error:
    print(f'Error occurred reading openmrs data {Error}')

finally:
    cursor.close()
    conn.close()


Unspecified: 1
Female: 3484
Male: 1800


In [17]:
#Data Exercise 2

import sqlite3
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt

conn = None
cursor = None

try:
    conn = sqlite3.connect('openmrs.db')
    cursor = conn.cursor()
    cursor.execute(''' 
        SELECT diagnosis.name as diagnosis_name, patient.gender as gender, (date('now') - patient.birthdate) as age
        FROM diagnosis 
        INNER JOIN encounter_diagnosis ON encounter_diagnosis.diagnosis_id =  diagnosis.id
        INNER JOIN encounter ON encounter.id = encounter_diagnosis.encounter_id
        INNER JOIN patient ON patient.id = encounter.patient_id
        ORDER BY diagnosis.name 
    ''')
    data = cursor.fetchall()
    diagnosis_to_axis_map = {}
    FACTOR = 17 # empirical

    default_dpi = mpl.rcParamsDefault['figure.dpi']
    mpl.rcParams['figure.dpi'] = default_dpi * FACTOR
    font = {'family' : 'DejaVu Sans', 'weight' : 'normal', 'size' : 4}
    mpl.rc('font', **font)
    
    # cannot plot diagnosis name, so need to convert it to a number
    current_diagnosis_number = 0 
    for datum in data:
        if datum[0] not in diagnosis_to_axis_map:
            diagnosis_to_axis_map[datum[0]] = current_diagnosis_number
            current_diagnosis_number = current_diagnosis_number + 1
    
    male_data = [[d[0], d[1], d[2], diagnosis_to_axis_map[d[0]]] for d in data if d[1].lower().strip() == 'm']
    female_data = [[d[0], d[1], d[2], diagnosis_to_axis_map[d[0]]] for d in data if d[1].lower().strip() == 'f']
    unspecified_gender = [[d[0], d[1], d[2], diagnosis_to_axis_map[d[0]]] for d in data if d[1].lower().strip() == '']
    
    fig = plt.figure() #figsize=(20, 15))
    ax = fig.add_subplot(111)
    
    #######
    import matplotlib.patches as mpatches

    classes = ['Male','Female','Unspecified']
    class_colours = ['b','pink','r']
    recs = []
    for i in range(0,len(class_colours)):
        recs.append(mpatches.Rectangle((0,0),1,1,fc=class_colours[i]))
    plt.legend(recs,classes,loc=4)
    #########
    
    print('This may take a minute or two. Please, be patient..')
    
    for index, person_data in enumerate([male_data, female_data, unspecified_gender]):
        for diagnosis_name, axis in diagnosis_to_axis_map.items():
            x = [d[2] for d in person_data if d[0].strip() == diagnosis_name]
            y = [axis] * len(x)
            
            color = ''
            
            if index == 0: 
                color= 'blue' #
            elif index == 1:
                color='pink' #female
            else:
                color='red' #gender unknow
                
            ax.scatter(x, y, color=color, s=10, edgecolors='none', alpha=0.9)
            
           

    
    ax.set_yticklabels(list(diagnosis_to_axis_map.keys()))
    ax.set_yticks(range(len(diagnosis_to_axis_map.values())))
    ax.set_title('Diagnosis vs Age, per gender')
    
    #ax.legend()
    ax.grid(False)
    plt.show()
    
   
    
except Error:
    print(f'Error occurred reading openmrs data {Error}')

finally:
    cursor.close()
    conn.close()


This may take a minute or two. Please, be patient..
